# 데이콘 소득 예측 경진대회

- 예측이지만, binary classification 문제

In [1]:
import matplotlib.pyplot as plt
import numpy as np
from glob import glob
import pandas as pd
import sys
from catboost import CatBoostClassifier
from tqdm.auto import tqdm

In [2]:
train=pd.read_csv("./data/train_cat_modified.csv")
train.head()

age workclass  fnlwgt  education_num      marital_status  \
0  3.465736   Private  309513             12  Married-civ-spouse   
1  3.496508   Private  205469             10  Married-civ-spouse   
2  3.828641   Private  149949             10  Married-civ-spouse   
3  3.135494   Private  193090             13       Never-married   
4  4.007333   Private   60193              9            Divorced   

        occupation   race     sex  capital_gain  capital_loss  hours_per_week  \
0     Craft-repair  White    Male             0             0              40   
1  Exec-managerial  White    Male             0             0              40   
2     Craft-repair  White    Male             0             0              40   
3     Adm-clerical  White  Female             0             0              30   
4     Adm-clerical  White  Female             0             0              40   

   target  education1  education2  education3  country_group1  country_group2  \
0       0           0           1           0               0               0   
1       1           0           1           0               0               0   
2       0           0           1           0               0               0   
3       0           0           1           0               0               0   
4       0           0           1           0               0               0   

   country_group3  country_group4  age_group  
0               1               0          1  
1               1               0          1  
2               1               0          1  
3               1               0          0  
4               1               0          1

In [3]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16707 entries, 0 to 16706
Data columns (total 20 columns):
 #   Column          Non-Null Count  Dtype  
---  ------          --------------  -----  
 0   age             16707 non-null  float64
 1   workclass       16707 non-null  object 
 2   fnlwgt          16707 non-null  int64  
 3   education_num   16707 non-null  int64  
 4   marital_status  16707 non-null  object 
 5   occupation      16707 non-null  object 
 6   race            16707 non-null  object 
 7   sex             16707 non-null  object 
 8   capital_gain    16707 non-null  int64  
 9   capital_loss    16707 non-null  int64  
 10  hours_per_week  16707 non-null  int64  
 11  target          16707 non-null  int64  
 12  education1      16707 non-null  int64  
 13  education2      16707 non-null  int64  
 14  education3      16707 non-null  int64  
 15  country_group1  16707 non-null  int64  
 16  country_group2  16707 non-null  int64  
 17  country_group3  16707 non-null 

In [4]:
train[['workclass','marital_status','occupation','race','sex']]=train[['workclass','marital_status','occupation','race','sex']].astype('category')

cat_features = ['workclass','marital_status','occupation','race','sex']


In [5]:
test=pd.read_csv("./data/test_cat_modified.csv")
test.head()

age     workclass  fnlwgt  education_num      marital_status  \
0  3.850148       Private  304133             10  Married-civ-spouse   
1  3.526361  Self-emp-inc  154227             10       Never-married   
2  3.433987     Local-gov  158291             13       Never-married   
3  3.332205       Private  183155             13  Married-civ-spouse   
4  3.988984     Local-gov  182543             10             Widowed   

        occupation   race     sex  capital_gain  capital_loss  hours_per_week  \
0  Exec-managerial  White    Male             0             0              45   
1            Sales  White    Male             0             0              75   
2     Craft-repair  White    Male          8614             0              40   
3   Prof-specialty  White    Male             0             0              55   
4     Adm-clerical  White  Female             0             0              40   

   education1  education2  education3  country_group1  country_group2  \
0           0           1           0               0               0   
1           0           1           0               0               0   
2           0           1           0               0               0   
3           0           1           0               0               0   
4           0           1           0               0               0   

   country_group3  country_group4  age_group  
0               1               0          1  
1               1               0          1  
2               1               0          1  
3               1               0          1  
4               0               1          1

In [6]:
test[['workclass','marital_status','occupation','race','sex']]=test[['workclass','marital_status','occupation','race','sex']].astype('category')

In [7]:
train_x=train.drop('target',axis=1)
train_y=train['target']

In [9]:
# GridSearchCV 를 이용해 모델들을 최적화시켜줍니다.
from tqdm.auto import tqdm


classifier = CatBoostClassifier(verbose=True,task_type="GPU",cat_features=cat_features)

params = {
        'n_estimators':[200,500,1000,1500],
        'learning_rate': [0.03, 0.1],
        'depth': [4, 6, 10],
        'l2_leaf_reg': [5, 7, 9],
        'one_hot_max_size':[3,12,16]
        
}


grid_result = classifier.grid_search(params,
                      X=train_x,
                      y=train_y,
                      plot=True
                      )


MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

0:	learn: 0.6676371	test: 0.6676364	best: 0.6676364 (0)	total: 26.6ms	remaining: 1.3s
1:	learn: 0.6453054	test: 0.6452663	best: 0.6452663 (1)	total: 49.3ms	remaining: 1.18s
2:	learn: 0.6248073	test: 0.6249346	best: 0.6249346 (2)	total: 70.5ms	remaining: 1.1s
3:	learn: 0.6064089	test: 0.6066603	best: 0.6066603 (3)	total: 92.3ms	remaining: 1.06s
4:	learn: 0.5896268	test: 0.5900844	best: 0.5900844 (4)	total: 113ms	remaining: 1.02s
5:	learn: 0.5742921	test: 0.5745635	best: 0.5745635 (5)	total: 134ms	remaining: 985ms
6:	learn: 0.5614144	test: 0.5619349	best: 0.5619349 (6)	total: 157ms	remaining: 963ms
7:	learn: 0.5479334	test: 0.5486567	best: 0.5486567 (7)	total: 179ms	remaining: 938ms
8:	learn: 0.5360433	test: 0.5369326	best: 0.5369326 (8)	total: 200ms	remaining: 911ms
9:	learn: 0.5237660	test: 0.5248675	best: 0.5248675 (9)	total: 221ms	remaining: 886ms
10:	learn: 0.5112807	test: 0.5123078	best: 0.5123078 (10)	total: 242ms	remaining: 859ms
11:	learn: 0.5019148	test: 0.5032355	best: 0.50323

48:	learn: 0.3165307	test: 0.3222339	best: 0.3222339 (48)	total: 1.1s	remaining: 22.4ms
49:	learn: 0.3155977	test: 0.3214210	best: 0.3214210 (49)	total: 1.12s	remaining: 0us
bestTest = 0.3214210314
bestIteration = 49
1:	loss: 0.3214210	best: 0.3214210 (1)	total: 4.45s	remaining: 7m 56s
0:	learn: 0.6600775	test: 0.6598225	best: 0.6598225 (0)	total: 22.7ms	remaining: 1.11s
1:	learn: 0.6297501	test: 0.6296526	best: 0.6296526 (1)	total: 43.3ms	remaining: 1.04s
2:	learn: 0.6032603	test: 0.6032110	best: 0.6032110 (2)	total: 64.6ms	remaining: 1.01s
3:	learn: 0.5804538	test: 0.5805007	best: 0.5805007 (3)	total: 84.2ms	remaining: 968ms
4:	learn: 0.5576017	test: 0.5577714	best: 0.5577714 (4)	total: 103ms	remaining: 930ms
5:	learn: 0.5387354	test: 0.5390408	best: 0.5390408 (5)	total: 123ms	remaining: 901ms
6:	learn: 0.5215965	test: 0.5219945	best: 0.5219945 (6)	total: 142ms	remaining: 872ms
7:	learn: 0.5042740	test: 0.5048225	best: 0.5048225 (7)	total: 161ms	remaining: 846ms
8:	learn: 0.4902521	t

48:	learn: 0.2753321	test: 0.2859764	best: 0.2859764 (48)	total: 1.08s	remaining: 22ms
49:	learn: 0.2751391	test: 0.2859387	best: 0.2859387 (49)	total: 1.1s	remaining: 0us
bestTest = 0.2859386944
bestIteration = 49
3:	loss: 0.2859387	best: 0.2859387 (3)	total: 8.05s	remaining: 7m 6s
0:	learn: 0.5914929	test: 0.5908088	best: 0.5908088 (0)	total: 22.4ms	remaining: 1.1s
1:	learn: 0.5179962	test: 0.5177811	best: 0.5177811 (1)	total: 44.1ms	remaining: 1.06s
2:	learn: 0.4671115	test: 0.4667538	best: 0.4667538 (2)	total: 65.9ms	remaining: 1.03s
3:	learn: 0.4327505	test: 0.4330202	best: 0.4330202 (3)	total: 87.6ms	remaining: 1.01s
4:	learn: 0.4063569	test: 0.4071403	best: 0.4071403 (4)	total: 109ms	remaining: 980ms
5:	learn: 0.3912795	test: 0.3928512	best: 0.3928512 (5)	total: 131ms	remaining: 959ms
6:	learn: 0.3742189	test: 0.3764543	best: 0.3764543 (6)	total: 152ms	remaining: 933ms
7:	learn: 0.3625825	test: 0.3654037	best: 0.3654037 (7)	total: 173ms	remaining: 907ms
8:	learn: 0.3504958	test:

41:	learn: 0.2798729	test: 0.2880527	best: 0.2880527 (41)	total: 867ms	remaining: 165ms
42:	learn: 0.2793879	test: 0.2876003	best: 0.2876003 (42)	total: 888ms	remaining: 144ms
43:	learn: 0.2788711	test: 0.2872181	best: 0.2872181 (43)	total: 907ms	remaining: 124ms
44:	learn: 0.2781658	test: 0.2866661	best: 0.2866661 (44)	total: 927ms	remaining: 103ms
45:	learn: 0.2777918	test: 0.2864708	best: 0.2864708 (45)	total: 948ms	remaining: 82.4ms
46:	learn: 0.2773824	test: 0.2860048	best: 0.2860048 (46)	total: 968ms	remaining: 61.8ms
47:	learn: 0.2769176	test: 0.2855443	best: 0.2855443 (47)	total: 988ms	remaining: 41.2ms
48:	learn: 0.2765138	test: 0.2851860	best: 0.2851860 (48)	total: 1.01s	remaining: 20.6ms
49:	learn: 0.2761452	test: 0.2850642	best: 0.2850642 (49)	total: 1.03s	remaining: 0us
bestTest = 0.2850641676
bestIteration = 49
5:	loss: 0.2850642	best: 0.2838563 (4)	total: 11.6s	remaining: 6m 44s
0:	learn: 0.6689086	test: 0.6689956	best: 0.6689956 (0)	total: 22.8ms	remaining: 1.11s
1:	lea

...

7:	learn: 0.3301275	test: 0.3313068	best: 0.3313068 (7)	total: 1.21s	remaining: 29.1s
8:	learn: 0.3201799	test: 0.3212274	best: 0.3212274 (8)	total: 1.42s	remaining: 30.1s
9:	learn: 0.3119948	test: 0.3129148	best: 0.3129148 (9)	total: 1.63s	remaining: 31s
10:	learn: 0.3057500	test: 0.3066239	best: 0.3066239 (10)	total: 1.84s	remaining: 31.6s
11:	learn: 0.3000070	test: 0.3009194	best: 0.3009194 (11)	total: 2.05s	remaining: 32.1s
12:	learn: 0.2963320	test: 0.2973503	best: 0.2973503 (12)	total: 2.09s	remaining: 30.1s
13:	learn: 0.2917342	test: 0.2934118	best: 0.2934118 (13)	total: 2.31s	remaining: 30.6s
14:	learn: 0.2883018	test: 0.2902934	best: 0.2902934 (14)	total: 2.51s	remaining: 30.9s
15:	learn: 0.2850756	test: 0.2875956	best: 0.2875956 (15)	total: 2.71s	remaining: 31.2s
16:	learn: 0.2824388	test: 0.2853397	best: 0.2853397 (16)	total: 2.92s	remaining: 31.5s
17:	learn: 0.2806017	test: 0.2836979	best: 0.2836979 (17)	total: 3.13s	remaining: 31.7s
18:	learn: 0.2789976	test: 0.2821200	bes

102:	learn: 0.2387807	test: 0.2626425	best: 0.2626425 (102)	total: 19.5s	remaining: 18.4s
103:	learn: 0.2386030	test: 0.2625332	best: 0.2625332 (103)	total: 19.7s	remaining: 18.2s
104:	learn: 0.2383487	test: 0.2625853	best: 0.2625332 (103)	total: 19.9s	remaining: 18s
105:	learn: 0.2382147	test: 0.2625508	best: 0.2625332 (103)	total: 20.1s	remaining: 17.8s
106:	learn: 0.2379933	test: 0.2624554	best: 0.2624554 (106)	total: 20.3s	remaining: 17.7s
107:	learn: 0.2374158	test: 0.2626111	best: 0.2624554 (106)	total: 20.5s	remaining: 17.5s
108:	learn: 0.2373478	test: 0.2626367	best: 0.2624554 (106)	total: 20.7s	remaining: 17.3s
109:	learn: 0.2369131	test: 0.2624942	best: 0.2624554 (106)	total: 20.9s	remaining: 17.1s
110:	learn: 0.2368272	test: 0.2624842	best: 0.2624554 (106)	total: 21.1s	remaining: 16.9s
111:	learn: 0.2366321	test: 0.2624536	best: 0.2624536 (111)	total: 21.3s	remaining: 16.8s
112:	learn: 0.2366129	test: 0.2624499	best: 0.2624499 (112)	total: 21.4s	remaining: 16.5s
113:	learn: 

194:	learn: 0.2256278	test: 0.2606453	best: 0.2606453 (194)	total: 36.9s	remaining: 945ms
195:	learn: 0.2256181	test: 0.2606442	best: 0.2606442 (195)	total: 37.1s	remaining: 757ms
196:	learn: 0.2255815	test: 0.2606566	best: 0.2606442 (195)	total: 37.3s	remaining: 568ms
197:	learn: 0.2255365	test: 0.2606846	best: 0.2606442 (195)	total: 37.5s	remaining: 379ms
198:	learn: 0.2255115	test: 0.2606934	best: 0.2606442 (195)	total: 37.7s	remaining: 190ms
199:	learn: 0.2253270	test: 0.2607382	best: 0.2606442 (195)	total: 37.9s	remaining: 0us
bestTest = 0.260644163
bestIteration = 195
Training on fold [2/3]
0:	learn: 0.5862450	test: 0.5869402	best: 0.5869402 (0)	total: 199ms	remaining: 39.7s
1:	learn: 0.5041135	test: 0.5057119	best: 0.5057119 (1)	total: 335ms	remaining: 33.2s
2:	learn: 0.4495056	test: 0.4518162	best: 0.4518162 (2)	total: 392ms	remaining: 25.8s
3:	learn: 0.4096510	test: 0.4126115	best: 0.4126115 (3)	total: 451ms	remaining: 22.1s
4:	learn: 0.3796704	test: 0.3838767	best: 0.3838767 

87:	learn: 0.2388698	test: 0.2658219	best: 0.2658219 (87)	total: 17.1s	remaining: 21.8s
88:	learn: 0.2387819	test: 0.2657838	best: 0.2657838 (88)	total: 17.4s	remaining: 21.6s
89:	learn: 0.2379417	test: 0.2658796	best: 0.2657838 (88)	total: 17.6s	remaining: 21.5s
90:	learn: 0.2378764	test: 0.2658737	best: 0.2657838 (88)	total: 17.8s	remaining: 21.3s
91:	learn: 0.2376105	test: 0.2658422	best: 0.2657838 (88)	total: 18s	remaining: 21.1s
92:	learn: 0.2374716	test: 0.2658223	best: 0.2657838 (88)	total: 18s	remaining: 20.7s
93:	learn: 0.2374062	test: 0.2657626	best: 0.2657626 (93)	total: 18.2s	remaining: 20.5s
94:	learn: 0.2371027	test: 0.2655811	best: 0.2655811 (94)	total: 18.4s	remaining: 20.4s
95:	learn: 0.2369090	test: 0.2655256	best: 0.2655256 (95)	total: 18.6s	remaining: 20.2s
96:	learn: 0.2366670	test: 0.2655224	best: 0.2655224 (96)	total: 18.9s	remaining: 20s
97:	learn: 0.2364244	test: 0.2654010	best: 0.2654010 (97)	total: 19.1s	remaining: 19.8s
98:	learn: 0.2363326	test: 0.2654128	b

180:	learn: 0.2230328	test: 0.2637330	best: 0.2633936 (170)	total: 35.7s	remaining: 3.74s
181:	learn: 0.2230228	test: 0.2637402	best: 0.2633936 (170)	total: 35.9s	remaining: 3.55s
182:	learn: 0.2225793	test: 0.2638152	best: 0.2633936 (170)	total: 36.1s	remaining: 3.35s
183:	learn: 0.2223090	test: 0.2638111	best: 0.2633936 (170)	total: 36.3s	remaining: 3.15s
184:	learn: 0.2222708	test: 0.2638245	best: 0.2633936 (170)	total: 36.5s	remaining: 2.96s
185:	learn: 0.2222659	test: 0.2638277	best: 0.2633936 (170)	total: 36.7s	remaining: 2.76s
186:	learn: 0.2222619	test: 0.2638345	best: 0.2633936 (170)	total: 36.9s	remaining: 2.57s
187:	learn: 0.2222331	test: 0.2638178	best: 0.2633936 (170)	total: 37.1s	remaining: 2.37s
188:	learn: 0.2222240	test: 0.2638208	best: 0.2633936 (170)	total: 37.3s	remaining: 2.17s
189:	learn: 0.2221742	test: 0.2637736	best: 0.2633936 (170)	total: 37.5s	remaining: 1.98s
190:	learn: 0.2215371	test: 0.2636488	best: 0.2633936 (170)	total: 37.7s	remaining: 1.78s
191:	learn

0.2643 {'depth': 10,
  'one_hot_max_size': 3,
  'l2_leaf_reg': 7,
  'iterations': 200,
  'learning_rate': 0.1

In [10]:
grid_result

{'params': {'depth': 10,
  'one_hot_max_size': 3,
  'l2_leaf_reg': 7,
  'iterations': 200,
  'learning_rate': 0.1},
 'cv_results': defaultdict(list,
             {'iterations': [0,
               1,
               2,
               3,
               4,
               5,
               6,
               7,
               8,
               9,
               10,
               11,
               12,
               13,
               14,
               15,
               16,
               17,
               18,
               19,
               20,
               21,
               22,
               23,
               24,
               25,
               26,
               27,
               28,
               29,
               30,
               31,
               32,
               33,
               34,
               35,
               36,
               37,
               38,
               39,
               40,
               41,
               42,
               43,
           

In [14]:
classifier = CatBoostClassifier(depth=10,l2_leaf_reg=7,
                                one_hot_max_size=3,learning_rate=0.1,iterations=200,
                                cat_features=cat_features,
                                verbose=True,task_type="GPU")

In [15]:
classifier.fit(train_x, train_y)
y_pred = classifier.predict(test)

0:	learn: 0.5821238	total: 56.4ms	remaining: 11.2s
1:	learn: 0.5024152	total: 116ms	remaining: 11.5s
2:	learn: 0.4462103	total: 176ms	remaining: 11.6s
3:	learn: 0.4052165	total: 237ms	remaining: 11.6s
4:	learn: 0.3745263	total: 298ms	remaining: 11.6s
5:	learn: 0.3531246	total: 357ms	remaining: 11.5s
6:	learn: 0.3361069	total: 417ms	remaining: 11.5s
7:	learn: 0.3237950	total: 475ms	remaining: 11.4s
8:	learn: 0.3133443	total: 535ms	remaining: 11.4s
9:	learn: 0.3053049	total: 594ms	remaining: 11.3s
10:	learn: 0.2981617	total: 652ms	remaining: 11.2s
11:	learn: 0.2931802	total: 709ms	remaining: 11.1s
12:	learn: 0.2881812	total: 771ms	remaining: 11.1s
13:	learn: 0.2844872	total: 829ms	remaining: 11s
14:	learn: 0.2815490	total: 889ms	remaining: 11s
15:	learn: 0.2781381	total: 948ms	remaining: 10.9s
16:	learn: 0.2758966	total: 1.01s	remaining: 10.8s
17:	learn: 0.2738404	total: 1.06s	remaining: 10.8s
18:	learn: 0.2711897	total: 1.13s	remaining: 10.7s
19:	learn: 0.2692233	total: 1.19s	remaining:

163:	learn: 0.1808285	total: 10.1s	remaining: 2.21s
164:	learn: 0.1806747	total: 10.1s	remaining: 2.15s
165:	learn: 0.1801299	total: 10.2s	remaining: 2.09s
166:	learn: 0.1799201	total: 10.3s	remaining: 2.03s
167:	learn: 0.1794732	total: 10.3s	remaining: 1.97s
168:	learn: 0.1791650	total: 10.4s	remaining: 1.9s
169:	learn: 0.1785533	total: 10.4s	remaining: 1.84s
170:	learn: 0.1781949	total: 10.5s	remaining: 1.78s
171:	learn: 0.1776942	total: 10.6s	remaining: 1.72s
172:	learn: 0.1775136	total: 10.6s	remaining: 1.66s
173:	learn: 0.1772206	total: 10.7s	remaining: 1.6s
174:	learn: 0.1769669	total: 10.8s	remaining: 1.53s
175:	learn: 0.1768545	total: 10.8s	remaining: 1.47s
176:	learn: 0.1766777	total: 10.9s	remaining: 1.41s
177:	learn: 0.1762091	total: 10.9s	remaining: 1.35s
178:	learn: 0.1758609	total: 11s	remaining: 1.29s
179:	learn: 0.1756077	total: 11.1s	remaining: 1.23s
180:	learn: 0.1754188	total: 11.1s	remaining: 1.17s
181:	learn: 0.1748002	total: 11.2s	remaining: 1.1s
182:	learn: 0.174

In [16]:
test

age     workclass  fnlwgt  education_num      marital_status  \
0      3.850148       Private  304133             10  Married-civ-spouse   
1      3.526361  Self-emp-inc  154227             10       Never-married   
2      3.433987     Local-gov  158291             13       Never-married   
3      3.332205       Private  183155             13  Married-civ-spouse   
4      3.988984     Local-gov  182543             10             Widowed   
...         ...           ...     ...            ...                 ...   
15076  3.401197     Local-gov  182926             10  Married-civ-spouse   
15077  3.663562       Private  176101             13  Married-civ-spouse   
15078  3.871201       Private  242406              7       Never-married   
15079  3.784190       Private  100584              9  Married-civ-spouse   
15080  3.401197       Private  345898              9       Never-married   

              occupation                race     sex  capital_gain  \
0        Exec-managerial               White    Male             0   
1                  Sales               White    Male             0   
2           Craft-repair               White    Male          8614   
3         Prof-specialty               White    Male             0   
4           Adm-clerical               White  Female             0   
...                  ...                 ...     ...           ...   
15076    Protective-serv               White    Male         15024   
15077       Craft-repair               White    Male             0   
15078  Machine-op-inspct               White    Male             0   
15079  Machine-op-inspct  Amer-Indian-Eskimo    Male             0   
15080       Craft-repair               Black    Male             0   

       capital_loss  hours_per_week  education1  education2  education3  \
0                 0              45           0           1           0   
1                 0              75           0           1           0   
2                 0              40           0           1           0   
3                 0              55           0           1           0   
4                 0              40           0           1           0   
...             ...             ...         ...         ...         ...   
15076             0              40           0           1           0   
15077             0              40           0           1           0   
15078             0              40           0           0           1   
15079             0              40           0           1           0   
15080             0              46           0           1           0   

       country_group1  country_group2  country_group3  country_group4  \
0                   0               0               1               0   
1                   0               0               1               0   
2                   0               0               1               0   
3                   0               0               1               0   
4                   0               0               0               1   
...               ...             ...             ...             ...   
15076               0               0               1               0   
15077               0               0               1               0   
15078               0               0               0               1   
15079               0               0               1               0   
15080               0               0               1               0   

       age_group  
0              1  
1              1  
2              1  
3              1  
4              1  
...          ...  
15076          1  
15077          1  
15078          1  
15079          1  
15080          1  

[15081 rows x 19 columns]

In [20]:
y_pred

array([1, 0, 1, ..., 0, 0, 0], dtype=int64)

In [21]:
y_pred.sum()

3177

In [22]:
submission = pd.read_csv('./data/sample_submission.csv')
submission.head()

id  target
0   0       0
1   1       0
2   2       0
3   3       0
4   4       0

In [23]:
submission['target']=y_pred
submission

id  target
0          0       1
1          1       0
2          2       1
3          3       1
4          4       0
...      ...     ...
15076  15076       1
15077  15077       0
15078  15078       0
15079  15079       0
15080  15080       0

[15081 rows x 2 columns]

In [24]:
submission.to_csv("./catboost_nodummy.csv",index=False)